<img src="https://github.com/LinkedEarth/Logos/blob/master/PyLiPD/pyLiPD_logo1_transparent.png?raw=true" width ="800">

# Working with ensembles in `PyLiPD`

## Authors

[Deborah Khider](https://orcid.org/0000-0001-7501-8430)

## Preamble

Ensembles are key to uncertainty quantification, and are a main reason for why the [LiPD](https://doi.org/10.5194/cp-12-1093-2016) format was created. LiPD stores tables of uncertainty ensembles (in particular, age), which `PyLiPD` can efficiently load for analysis. This notebook describes how `PyLiPD` handles such age ensembles.

### Goals

* Reading an ensemble from a LiPD object

Reading Time: 5 minutes

### Keywords

LiPD, age uncertainty, age ensembles

### Pre-requisites

None. This tutorial assumes basic knowledge of Python and Pandas. If you are not familiar with this coding language and this particular library, check out this tutorial: http://linked.earth/ec_workshops_py/.

### Relevant Packages

pylipd

## Data Description

This notebook uses the following datasets, in LiPD format:

- McCabe-Glynn, S., Johnson, K., Strong, C. et al. Variable North Pacific influence on drought in southwestern North America since AD 854. Nature Geosci 6, 617–621 (2013). https://doi.org/10.1038/ngeo1862

- Lawrence, K. T., Liu, Z. H., & Herbert, T. D. (2006). Evolution of the eastern tropical Pacific through Plio-Pleistocne glaciation. Science, 312(5770), 79-83.

## Demonstration

### Extracting ensemble information

In [1]:
from pylipd.lipd import LiPD

In [2]:
D = LiPD()
data_path = ['../data/Crystal.McCabe-Glynn.2013.lpd', '../data/ODP846.Lawrence.2006.lpd']
D.load(data_path)

Loading 2 LiPD files


100%|████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00,  2.79it/s]

Loaded..


In [3]:
names = D.get_all_dataset_names()
print(names)

['Crystal.McCabe-Glynn.2013', 'ODP846.Lawrence.2006']


To load the ensemble tables for all the files:

<div class="alert alert-warning">
This may take a few minutes since we need to load matrices containing 1000 columns and a few hundred rows into memory. Although it is possible to load all the ensemble tables present in all the datasets, we strongly suggest against it (you will run out of memory). Instead, open dataset by dataset as we will demonstrate in this notebook.
</div>

In [4]:
%time
df = D.get_ensemble_tables()

df

CPU times: user 2 µs, sys: 1 µs, total: 3 µs
Wall time: 4.77 µs


datasetName  \
0  Crystal.McCabe-Glynn.2013   
1       ODP846.Lawrence.2006   

                                       ensembleTable ensembleVariableName  \
0  http://linked.earth/lipd/Crystal.McCabe-Glynn....                 Year   
1     http://linked.earth/lipd/chron0model0ensemble0                  age   

                              ensembleVariableValues ensembleVariableUnits  \
0  [[2007.0, 2007.0, 2008.0, 2007.0, 2007.0, 2007...                 yr AD   
1  [[4.0, 4.0, 4.0, 4.0, 4.0, 4.0, 4.0, 4.0, 4.0,...                kyr BP   

  ensembleDepthName                                ensembleDepthValues  \
0             depth  [0.1, 0.15, 0.2, 0.25, 0.3, 0.35, 0.4, 0.45, 0...   
1             depth  [0.12, 0.23, 0.33, 0.43, 0.53, 0.63, 0.73, 0.8...   

  ensembleDepthUnits notes  
0                 mm  None  
1                  m  None

The dataframes return the following information:

* `datasetName`: The name of the dataset
* `ensembleTable`: The ensemble tables associated with the dataset. If more than one ensembleTable is available for the record, then each table will be contained on a different row
* `ensembleVariableName`: The name of the ensemble variable. Most likely, it will be a variant of 'age' or 'year'
* `ensembleVariableValues`: The values on the ensembles
* `ensembleVariableUnits`: The units associated with the time variable
* `ensembleDepthName`: The name of the depth vector
* `ensembleDepthValues`: The values for the depth axis. This is particularly useful when matching a ensemble table to a particular variable
* `ensembleDepthUnits`: The units for the depth. 
* `notes`: Notes regarding how the model was obtained/done. 

If interested in only one dataset (see the warning):

In [5]:
df = D.get_ensemble_tables(dsname=names[0])

df

datasetName  \
0  Crystal.McCabe-Glynn.2013   

                                       ensembleTable ensembleVariableName  \
0  http://linked.earth/lipd/Crystal.McCabe-Glynn....                 Year   

                              ensembleVariableValues ensembleVariableUnits  \
0  [[2007.0, 2007.0, 2008.0, 2007.0, 2007.0, 2007...                 yr AD   

  ensembleDepthName                                ensembleDepthValues  \
0             depth  [0.1, 0.15, 0.2, 0.25, 0.3, 0.35, 0.4, 0.45, 0...   

  ensembleDepthUnits notes  
0                 mm  None

If you know the variable name:

In [6]:
df = D.get_ensemble_tables(ensembleVarName='age')

df

datasetName                                   ensembleTable  \
0  ODP846.Lawrence.2006  http://linked.earth/lipd/chron0model0ensemble0   

  ensembleVariableName                             ensembleVariableValues  \
0                  age  [[4.0, 4.0, 4.0, 4.0, 4.0, 4.0, 4.0, 4.0, 4.0,...   

  ensembleVariableUnits ensembleDepthName  \
0                kyr BP             depth   

                                 ensembleDepthValues ensembleDepthUnits notes  \
0  [0.12, 0.23, 0.33, 0.43, 0.53, 0.63, 0.73, 0.8...                  m  None   

  methodobj methods  
0      None    None

### Working with the PaleoData

For this part of the demo, let's work with only the Crystal Cave record. We can pass the name of the dataset directly to the function through the `dsname` parameter. In this case, the name is the first entry (index 0, remember that Python uses zero-index) in the `names` list that we obtained previously:

In [7]:
df = D.get_ensemble_tables(dsname=names[0])
df

datasetName  \
0  Crystal.McCabe-Glynn.2013   

                                       ensembleTable ensembleVariableName  \
0  http://linked.earth/lipd/Crystal.McCabe-Glynn....                 Year   

                              ensembleVariableValues ensembleVariableUnits  \
0  [[2007.0, 2007.0, 2008.0, 2007.0, 2007.0, 2007...                 yr AD   

  ensembleDepthName                                ensembleDepthValues  \
0             depth  [0.1, 0.15, 0.2, 0.25, 0.3, 0.35, 0.4, 0.45, 0...   

  ensembleDepthUnits notes  
0                 mm  None

In [9]:
df_ts = D.get_timeseries_essentials(dsnames=names[0])

df_ts

dataSetName archiveType  geo_meanLat  geo_meanLon  \
0  Crystal.McCabe-Glynn.2013  Speleothem        36.59      -118.82   

   geo_meanElev paleoData_variableName  \
0        1386.0                   d18o   

                                    paleoData_values paleoData_units  \
0  [-8.01, -8.23, -8.61, -8.54, -8.6, -9.08, -8.9...          permil   

  paleoData_proxy paleoData_proxyGeneral time_variableName  \
0            None                   None               age   

                                         time_values time_units  \
0  [2007.7, 2007.0, 2006.3, 2005.6, 2004.9, 2004....      yr AD   

  depth_variableName                                       depth_values  \
0              depth  [0.05, 0.1, 0.15, 0.2, 0.25, 0.3, 0.35, 0.4, 0...   

  depth_units  
0          mm

To learn  how to use these two tables to create a [Pyleoclim `EnsembleSeries`](https://pyleoclim-util.readthedocs.io/en/latest/core/api.html#ensembleseries-pyleoclim-ensembleseries) object and use it for analysis and visualization, see [this tutorial](http://linked.earth/PyleoTutorials/notebooks/L1_working_with_age_ensembles.html) 